In [1]:
!pip install transformers
!pip install pandas
!pip install torch

In [2]:

from huggingface_hub import notebook_login
import pandas as pd
from transformers import LlamaTokenizer, LlamaForCausalLM, AutoTokenizer, AutoModelForCausalLM, pipeline
import torch
import transformers
from tqdm import tqdm
from torch.utils.data import Dataset

In [3]:

import pandas as pd
from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline
import torch
import tqdm

# Check if GPU is available and set the device
if torch.cuda.is_available():
    device = torch.device("cuda")
    print("Using GPU")
else:
    device = torch.device("cpu")
    print("Using CPU")
token = ""  # Replace with your token

# Load the model and tokenizer
model_name = "meta-llama/Llama-2-7b-chat-hf"  # Use the same model as before

model = AutoModelForCausalLM.from_pretrained(model_name, use_auth_token=token, torch_dtype=torch.float16, device_map="auto")
tokenizer = AutoTokenizer.from_pretrained(model_name, use_auth_token=token)

pipeline = pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer,
    torch_dtype=torch.float16,
    device_map="auto",
)

# Define the query_model function to generate short answers
def query_model(prompt, temperature=0, max_length=20):
    sequences = pipeline(
        prompt,
        do_sample=False,  # No randomness, for deterministic answers
        temperature=temperature,  # No randomness for deterministic output
        max_new_tokens=max_length,  # Limit output length to 50 tokens
        return_full_text=False,
        pad_token_id=tokenizer.eos_token_id
    )
    print("*")
    answer = sequences[0]['generated_text'].strip()
    return answer

Using GPU


/usr/local/lib/python3.10/dist-packages/transformers/models/auto/auto_factory.py:469: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


config.json:   0%|          | 0.00/614 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/26.8k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/transformers/models/auto/tokenization_auto.py:786: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/1.62k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

In [4]:
df = pd.read_csv('file.csv')

generated_answers = []

# Loop through each row in the dataset
for index, row in tqdm.tqdm(df.iterrows(), total=len(df)):
    try:
        question = row['prompting_few_P3']
        print(question)
        print("**")
        # Query the model with the current question
        response = query_model(question, temperature=0)
        print(response)
        print("**")
        generated_answers.append(response)
    except Exception as e:
        print(f"An error occurred for row {index}: {e}")
        generated_answers.append(None)  # Append None for failed generations

# Add the generated answers to the dataframe
df['answer'] = generated_answers

# Save the dataframe with the answers to a new Excel file
df.to_csv('file.csv', index=False)

print("Model answers have been saved to 'DiseaseDecipher_with_Answers.csv'.")


  0%|          | 0/3200 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:567: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:572: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


Given the symptoms of the patient, choose the most likely disease from the options below. Respond with the disease name only.

Example 1:
Q: A patient is presenting with the following symptoms: Sleepiness, Fatigue, Apnea, Headache. Based on these symptoms, which of the following diseases is the most likely diagnosis?
1) Poisoning due to analgesics 2) Adrenal cancer 3) Narcolepsy 4) Chronic back pain
Answer: Narcolepsy

Example 2:
Q: A patient is presenting with the following symptoms: Palpitations, Sharp chest pain, Dizziness, Irregular heartbeat, Shortness of breath. Based on these symptoms, which of the following diseases is the most likely diagnosis? 
1) Spondylitis 2) Arrhythmia 3) Chronic ulcer 4) Cervical disorder
Answer: Arrhythmia

Q: A patient is presenting with the following symptoms: Anxiety and nervousness, Depression, Shortness of breath. Based on these symptoms, which of the following diseases is the most likely diagnosis?
1) Panic disorder 2) Tinnitus of unknown cause 3)

  0%|          | 1/3200 [00:02<1:50:17,  2.07s/it]

*
Panic disorder
**
Given the symptoms of the patient, choose the most likely disease from the options below. Respond with the disease name only.

Example 1:
Q: A patient is presenting with the following symptoms: Sleepiness, Fatigue, Apnea, Headache. Based on these symptoms, which of the following diseases is the most likely diagnosis?
1) Poisoning due to analgesics 2) Adrenal cancer 3) Narcolepsy 4) Chronic back pain
Answer: Narcolepsy

Example 2:
Q: A patient is presenting with the following symptoms: Palpitations, Sharp chest pain, Dizziness, Irregular heartbeat, Shortness of breath. Based on these symptoms, which of the following diseases is the most likely diagnosis? 
1) Spondylitis 2) Arrhythmia 3) Chronic ulcer 4) Cervical disorder
Answer: Arrhythmia

Q: A patient is presenting with the following symptoms: Anxiety and nervousness, Depression, Shortness of breath. Based on these symptoms, which of the following diseases is the most likely diagnosis?
1) Tinnitus of unknown cause 

  0%|          | 2/3200 [00:02<1:04:18,  1.21s/it]

...

100%|█████████▉| 3199/3200 [36:11<00:00,  1.64it/s]

*
Otosclerosis
**
Given the symptoms of the patient, choose the most likely disease from the options below. Respond with the disease name only.

Example 1:
Q: A patient is presenting with the following symptoms: Sleepiness, Fatigue, Apnea, Headache. Based on these symptoms, which of the following diseases is the most likely diagnosis?
1) Poisoning due to analgesics 2) Adrenal cancer 3) Narcolepsy 4) Chronic back pain
Answer: Narcolepsy

Example 2:
Q: A patient is presenting with the following symptoms: Palpitations, Sharp chest pain, Dizziness, Irregular heartbeat, Shortness of breath. Based on these symptoms, which of the following diseases is the most likely diagnosis? 
1) Spondylitis 2) Arrhythmia 3) Chronic ulcer 4) Cervical disorder
Answer: Arrhythmia

Q: A patient is presenting with the following symptoms: Diminished hearing, Dizziness, Plugged feeling in ear, Ear pain, Elbow weakness, Nailbiting. Based on these symptoms, which of the following diseases is the most likely diagnos

100%|██████████| 3200/3200 [36:12<00:00,  1.47it/s]

*
Otosclerosis
**


Model answers have been saved to 'DiseaseDecipher_with_Answers.csv'.
